In [1]:
from insolAPI.WebAPI import API
import simplejson as json
import pandas as pd
import pendulum as pdl
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from datetime import datetime, timedelta
import warnings
from tqdm import tqdm
import sys
from tabulate import tabulate
from pytz import timezone

In [2]:
time_args = dict(
    start=pdl.yesterday().subtract(weeks=1).to_datetime_string(),
    stop=(pdl.now()).to_datetime_string(),
    timezone = timezone('Europe/Zurich')
)

def read_json_config():
    """
    Read the config.json file and return the api key
    """
    with open("config.json") as f:
        config_data = json.load(f)

    installations = {}

    # Iterate through locations
    locations = config_data['locations']
    for location in locations:
        # Store details in a dictionary
        location_details = {
            'id': location['id'],
            'name': location['name'],
            'latitude': location['latitude'],
            'longitude': location['longitude'],
            'wind_threshold': location['wind_threshold'],
            'high_temperature_threshold': location['high_temperature_threshold'],
            'has_a_screen': location['has_a_screen'],
        }
        installations[location['name']] = location_details
    return installations, [config_data['api_key'], config_data['api_url']]


installation_path = "C:/Users/Insolight/Desktop/InsolReports/Scripts"
with open(installation_path + "/local.json") as f:
    local_data = json.load(f)
api = API(local_data["API_user"], local_data["API_pwd"], dev_space=False)

list_sensor = [
    "PAR",
    "IRRAD",
    "GII",
    "DNI",
    "DHI",
    "TEMP",
    "HUMI",
    "RAIN",
    "RAIN_TYPE",
    "RAIN_ACCUMULATED",
    "WIND",
    "WIND_DIR",
    "VIRTUAL",
    "LEAF_TEMP"
]

dict_instal = {
    "Etchelecu": 26,
    "Agroscope Series": 24,
    "Agroscope Berries": 25,
    "Bioschmid": 23,
}

In [3]:
logs_joined = {}
dict_list_theoretical = {}
for instal in tqdm(dict_instal):
    logs_joined[instal] = {}
    dict_list_theoretical[instal] = []
    sensor_number = 0
    for sensor_type in api.SensorsTypes:
        if str(sensor_type).split(".")[1] in list_sensor:
            with warnings.catch_warnings():
                warnings.simplefilter("ignore", category=UserWarning)
                logs_joined[instal][list_sensor[sensor_number]] = api.get_sensor_channels_logs_joined(**time_args,sensor_type=sensor_type, install=dict_instal[instal])
                sensor_number += 1
                try:
                    theoretical_sensor = api.get_sensor_channels(sensor_type=sensor_type, install=dict_instal[instal])
                    theoretical_sensor = theoretical_sensor[theoretical_sensor["deleted_at"].isna()].sensor_name.unique()
                    dict_list_theoretical[instal].extend(theoretical_sensor)
                except:
                    pass

100%|██████████| 4/4 [00:54<00:00, 13.59s/it]


In [4]:
unique_sensors = {}
logs_joined_unique = {}
last_log = {}
for instal in dict_instal:
    print(instal)
    unique_sensors[instal] = []
    for sensor_type in logs_joined[instal]:
        try:
            unique_sensors[instal].extend(logs_joined[instal][sensor_type]["sensor_name"].unique())
        except :
            pass
    unique_sensors[instal] = list(set(unique_sensors[instal]))
    logs_joined_unique[instal] = {}
    for sensor_type in logs_joined[instal]:
        for unique_sensor in unique_sensors[instal]:
            try:
                if unique_sensor in logs_joined[instal][sensor_type]["sensor_name"].unique():
                    logs_joined_unique[instal][unique_sensor] = logs_joined[instal][sensor_type].loc[logs_joined[instal][sensor_type]["sensor_name"] == unique_sensor]
                    logs_joined_unique[instal][unique_sensor].index = logs_joined_unique[instal][unique_sensor].index.round('min')
                    logs_joined_unique[instal][unique_sensor] = logs_joined_unique[instal][unique_sensor].loc[~logs_joined_unique[instal][unique_sensor].index.duplicated(keep='first')]
            except :
                pass

    for sensor in logs_joined_unique[instal]:
        logs_joined_unique[instal][sensor] = logs_joined_unique[instal][sensor].dropna(subset=[logs_joined_unique[instal][sensor].columns[1]])

    last_log[instal] = {}
    for sensor in dict_list_theoretical[instal]:
        try:
            last_log[instal][sensor] = logs_joined_unique[instal][sensor].index[-1]
        except:
            last_log[instal][sensor] = "no log"
        try:
            if last_log[instal][sensor] > pdl.now().subtract(minutes=10):
                last_log[instal][sensor] = "up to date"
        except:
            pass

Etchelecu
Agroscope Series
Agroscope Berries
Bioschmid


In [11]:
#sort the sensors by the last log
for instal in last_log:
    last_log[instal] = {k: v for k, v in sorted(last_log[instal].items(), key=lambda item: item[1])}

In [12]:
for i in last_log:
    print(i)
    print(tabulate(last_log[i].items(), headers=["Sensor", "Last log"], tablefmt="github"))
    print("\n")

Etchelecu
| Sensor                | Last log   |
|-----------------------|------------|
| PAR02_control         | up to date |
| PAR01_control         | up to date |
| PAR02_EXT             | up to date |
| PAR01_EXT             | up to date |
| PAR04_Insolagrin      | up to date |
| PAR03_Insolagrin      | up to date |
| PAR02_Insolagrin      | up to date |
| PAR01_Insolagrin      | up to date |
| GHI_01_EXT            | up to date |
| TRH_bottom_control    | up to date |
| TRH_top_control       | up to date |
| TRH_bottom_EXT        | up to date |
| TRH_top_EXT           | up to date |
| TRH_bottom_Insolagrin | up to date |
| TRH_top_Insolagrin    | up to date |
| RAIN_EXT              | up to date |
| WIND02_EXT            | up to date |
| WIND01_EXT            | up to date |


Agroscope Series
| Sensor                            | Last log   |
|-----------------------------------|------------|
| rain                              | no log     |
| leaf_temp_FS1                     | 

In [10]:
for i, val in last_log.items():
    print(val)


{'PAR02_control': 'up to date', 'PAR01_control': 'up to date', 'PAR02_EXT': 'up to date', 'PAR01_EXT': 'up to date', 'PAR04_Insolagrin': 'up to date', 'PAR03_Insolagrin': 'up to date', 'PAR02_Insolagrin': 'up to date', 'PAR01_Insolagrin': 'up to date', 'GHI_01_EXT': 'up to date', 'TRH_bottom_control': 'up to date', 'TRH_top_control': 'up to date', 'TRH_bottom_EXT': 'up to date', 'TRH_top_EXT': 'up to date', 'TRH_bottom_Insolagrin': 'up to date', 'TRH_top_Insolagrin': 'up to date', 'RAIN_EXT': 'up to date', 'WIND02_EXT': 'up to date', 'WIND01_EXT': 'up to date'}
{'PAR_EXT_06': 'up to date', 'PAR_EXT_05': 'up to date', 'PAR_EXT_04': 'up to date', 'PAR01_Nursery': 'up to date', 'PAR01_GT1_tunnel': 'up to date', 'PAR01_GT_tunnel': 'up to date', 'PAR01_TX_tunnel': 'up to date', 'PAR_umbrella': 'up to date', 'PAR_umbrella_strawb': 'up to date', 'PAR_STRAWB': 'up to date', 'PAR_ext_bis': 'up to date', 'PAR8': 'up to date', 'PAR7': 'up to date', 'PAR6': 'up to date', 'PAR5': 'up to date', 'PAR

In [49]:
time_diff = {}
time_diff_mean = {}
for instal in logs_joined_unique:
    time_diff[instal] = {}
    time_diff_mean[instal] = {}
    for sensor in logs_joined_unique[instal]:
        time_diff_mean[instal][sensor] = logs_joined_unique[instal][sensor].index.to_series().diff()[1:].mean().total_seconds()
        time_diff_mean[instal][sensor] = logs_joined_unique[instal][sensor].index.to_series().diff()[1:]

KeyboardInterrupt: 

# Plot the distribution of the time between logs

In [51]:
time_diff = {}
for instal in dict_instal:
    time_diff[instal] = {}
    for unique_sensor in logs_joined_unique[instal]:
        #compute the time difference between two logs in seconds
        time_diff[instal][unique_sensor] = logs_joined_unique[instal][unique_sensor].index.to_series().diff()[1:]

In [ ]:
for instal in dict_instal:
    total_num_sensors = len(unique_sensors[instal])
    num_rows = total_num_sensors // 6
    fig = plt.figure()
    fig.set_figheight(7*num_rows)
    fig.set_figwidth(20)
    fig.suptitle(instal)
    for unique_sensor in unique_sensors[instal]:
        ax = fig.add_subplot(num_rows + 1, 6, unique_sensors[instal].index(unique_sensor) + 1)
        ax.hist(time_diff[instal][unique_sensor].dropna().dt.total_seconds(), bins=10, range=(61, 10000))
        ax.set_title(unique_sensor)
        ax.set_xlim(61, 10000)
        ax.grid(True)
        ax.set_yscale('log')
    fig.tight_layout()

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

for instal in dict_instal:
    total_num_sensors = len(unique_sensors[instal])
    num_rows = total_num_sensors // 6

    fig = make_subplots(rows=num_rows + 1, cols=6, subplot_titles=unique_sensors[instal], shared_yaxes=True)
    fig.update_layout(title_text=instal)
    #set the height of the figure
    fig.update_layout(height=300*num_rows)

    for i, unique_sensor in enumerate(unique_sensors[instal]):
        row_num = i // 6 + 1
        col_num = i % 6 + 1

        trace = go.Histogram(
            x=time_diff[instal][unique_sensor].dropna().dt.total_seconds(),
            nbinsx=10,
            xbins=dict(start=61, end=10000),
            name=unique_sensor,
        )

        fig.add_trace(trace, row=row_num, col=col_num)

        fig.update_xaxes(row=row_num, col=col_num)
        fig.update_yaxes(row=row_num, col=col_num, type="log")

    fig.update_layout(showlegend=False)
    # fig.update_layout(subplot_titles_text={'size': 10})
    fig.show()
    #save the figure as a html file
    fig.write_html("hist log frequency/" + instal + "_time_diff.html")


In [35]:
test = api.get_sensor_channels(sensor_type=api.SensorsTypes.LEAF_TEMP, install=24)

In [36]:
a = test[test["deleted_at"].isna()]
a

gateway_id  local_channel_id                   created_at deleted_at   
id                                                                          
995          29               769  2023-08-25T10:28:50.000000Z       None  \
994          29               768  2023-08-25T10:28:50.000000Z       None   
993          29               767  2023-08-25T10:28:50.000000Z       None   
992          29               766  2023-08-25T10:28:50.000000Z       None   
991          29               765  2023-08-25T10:28:50.000000Z       None   
..          ...               ...                          ...        ...   
770          29               669  2023-07-29T00:24:19.000000Z       None   
769          29               668  2023-07-29T00:24:19.000000Z       None   
768          29               667  2023-07-29T00:24:19.000000Z       None   
767          29               666  2023-07-29T00:24:18.000000Z       None   
766          29               665  2023-07-29T00:24:18.000000Z       None   

                           sensor_name channel_name  sensor_type   
id                                                                 
995  LeafTemp_Tulameen_E_NurseryTunnel  temp_sensor          234  \
994  LeafTemp_Tulameen_E_NurseryTunnel     temp_raw          234   
993  LeafTemp_Tulameen_E_NurseryTunnel     temp_max          234   
992  LeafTemp_Tulameen_E_NurseryTunnel     temp_min          234   
991  LeafTemp_Tulameen_E_NurseryTunnel     temp_avg          234   
..                                 ...          ...          ...   
770                      leaf_temp_FS1  temp_sensor          234   
769                      leaf_temp_FS1     temp_raw          234   
768                      leaf_temp_FS1     temp_max          234   
767                      leaf_temp_FS1     temp_min          234   
766                      leaf_temp_FS1     temp_avg          234   

     position_bitfield  brand           model serial_number   
id                                                            
995                 22  Calex  InfraredSensor       unknown  \
994                 22  Calex  InfraredSensor       unknown   
993                 22  Calex  InfraredSensor       unknown   
992                 22  Calex  InfraredSensor       unknown   
991                 22  Calex  InfraredSensor       unknown   
..                 ...    ...             ...           ...   
770                 22  Calex  InfraredSensor      OL091594   
769                 22  Calex  InfraredSensor      OL091594   
768                 22  Calex  InfraredSensor      OL091594   
767                 22  Calex  InfraredSensor      OL091594   
766                 22  Calex  InfraredSensor      OL091594   

    configuration_json  address  dx  dy  dz  nx  ny zones_ids   
id                                                              
995                 []      136   0   0   0   1   1      [27]  \
994                 []      136   0   0   0   1   1      [27]   
993                 []      136   0   0   0   1   1      [27]   
992                 []      136   0   0   0   1   1      [27]   
991                 []      136   0   0   0   1   1      [27]   
..                 ...      ...  ..  ..  ..  ..  ..       ...   
770                 []      130   0   0   0   1   1        []   
769                 []      130   0   0   0   1   1        []   
768                 []      130   0   0   0   1   1        []   
767                 []      130   0   0   0   1   1        []   
766                 []      130   0   0   0   1   1        []   

          zones_names  
id                     
995  [Nursery Tunnel]  
994  [Nursery Tunnel]  
993  [Nursery Tunnel]  
992  [Nursery Tunnel]  
991  [Nursery Tunnel]  
..                ...  
770                []  
769                []  
768                []  
767                []  
766                []  

[75 rows x 20 columns]

In [37]:
list = a.index.tolist()
list

[995,
 994,
 993,
 992,
 991,
 990,
 989,
 988,
 987,
 986,
 985,
 984,
 983,
 982,
 981,
 980,
 979,
 978,
 977,
 976,
 975,
 974,
 973,
 972,
 971,
 970,
 969,
 968,
 967,
 966,
 965,
 964,
 963,
 962,
 961,
 960,
 959,
 958,
 957,
 956,
 955,
 954,
 953,
 952,
 951,
 950,
 949,
 948,
 947,
 946,
 945,
 944,
 943,
 942,
 941,
 940,
 939,
 938,
 937,
 936,
 798,
 797,
 796,
 795,
 794,
 775,
 774,
 773,
 772,
 771,
 770,
 769,
 768,
 767,
 766]

In [38]:
test

gateway_id  local_channel_id                   created_at   
id                                                               
995          29               769  2023-08-25T10:28:50.000000Z  \
994          29               768  2023-08-25T10:28:50.000000Z   
993          29               767  2023-08-25T10:28:50.000000Z   
992          29               766  2023-08-25T10:28:50.000000Z   
991          29               765  2023-08-25T10:28:50.000000Z   
..          ...               ...                          ...   
167          29               107  2022-09-15T15:31:12.000000Z   
166          29               106  2022-09-15T15:31:11.000000Z   
165          29               105  2022-09-15T15:31:11.000000Z   
164          29               104  2022-09-15T15:31:11.000000Z   
163          29               103  2022-09-15T15:31:07.000000Z   

                      deleted_at                        sensor_name   
id                                                                    
995                         None  LeafTemp_Tulameen_E_NurseryTunnel  \
994                         None  LeafTemp_Tulameen_E_NurseryTunnel   
993                         None  LeafTemp_Tulameen_E_NurseryTunnel   
992                         None  LeafTemp_Tulameen_E_NurseryTunnel   
991                         None  LeafTemp_Tulameen_E_NurseryTunnel   
..                           ...                                ...   
167  2022-12-14T09:40:24.000000Z                         leaf_temp1   
166  2022-12-14T09:40:24.000000Z                         leaf_temp1   
165  2022-12-14T09:40:24.000000Z                         leaf_temp1   
164  2022-12-14T09:40:24.000000Z                         leaf_temp1   
163  2022-12-14T09:40:24.000000Z                         leaf_temp1   

    channel_name  sensor_type  position_bitfield  brand           model   
id                                                                        
995  temp_sensor          234                 22  Calex  InfraredSensor  \
994     temp_raw          234                 22  Calex  InfraredSensor   
993     temp_max          234                 22  Calex  InfraredSensor   
992     temp_min          234                 22  Calex  InfraredSensor   
991     temp_avg          234                 22  Calex  InfraredSensor   
..           ...          ...                ...    ...             ...   
167  temp_sensor          234                  6  Calex  InfraredSensor   
166     temp_raw          234                  6  Calex  InfraredSensor   
165     temp_max          234                  6  Calex  InfraredSensor   
164     temp_min          234                  6  Calex  InfraredSensor   
163     temp_avg          234                  6  Calex  InfraredSensor   

    serial_number configuration_json  address  dx  dy  dz  nx  ny zones_ids   
id                                                                            
995       unknown                 []      136   0   0   0   1   1      [27]  \
994       unknown                 []      136   0   0   0   1   1      [27]   
993       unknown                 []      136   0   0   0   1   1      [27]   
992       unknown                 []      136   0   0   0   1   1      [27]   
991       unknown                 []      136   0   0   0   1   1      [27]   
..            ...                ...      ...  ..  ..  ..  ..  ..       ...   
167      OL091594                 []      130   0   0   0   1   1       [2]   
166      OL091594                 []      130   0   0   0   1   1       [2]   
165      OL091594                 []      130   0   0   0   1   1       [2]   
164      OL091594                 []      130   0   0   0   1   1       [2]   
163      OL091594                 []      130   0   0   0   1   1       [2]   

          zones_names  
id                     
995  [Nursery Tunnel]  
994  [Nursery Tunnel]  
993  [Nursery Tunnel]  
992  [Nursery Tunnel]  
991  [Nursery Tunnel]  
..                ...  
167       [main_zone]  
16